# gpCAM Test Notebook
In this notebook we will go through many features of gpCAM. Work through it 
and you are ready for your own autonomous experiment. 

## This first cell has nothing to do with gpCAM, it's just a function to plot some results later

In [1]:
import plotly.graph_objects as go
import numpy as np
def plot(x,y,z,data = None):
    fig = go.Figure()
    fig.add_trace(go.Surface(x = x, y = y,z=z))
    if data is not None: 
        fig.add_trace(go.Scatter3d(x=data[:,0], y=data[:,1], z=data[:,2],
                                   mode='markers'))

    fig.update_layout(title='Posterior Mean', autosize=True,
                  width=800, height=800,
                  margin=dict(l=65, r=50, b=65, t=90))


    fig.show()

## Here we want to define some points at which we will predict, still has nothing to do with gpCAM 

In [2]:
x_pred = np.zeros((10000,2))
x = np.linspace(0,10,100)
y = np.linspace(0,10,100)
x,y = np.meshgrid(x,y)
counter = 0
for i in  range(100):
    for j in range(100):
        x_pred[counter] = np.array([x[i,j],y[i,j]])
        counter += 1

## Let's get after it by setting up a Single-Task GP Autonomous Data Acquisition Run

In [3]:
def optional_acq_func(x,obj):
    #this acquisition function makes the autonomous experiment a Bayesian optimization
    a = 3.0 #3.0 for 95 percent confidence interval
    mean = obj.posterior_mean(x)["f(x)"]
    cov = obj.posterior_covariance(x)["v(x)"]
    return mean + a * cov
def optional_cost_function(origin,x,arguments = None):
    #cost pf l1 motion in the input space
    offset = arguments["offset"]
    slope = arguments["slope"]
    d = np.abs(np.subtract(origin,x))
    c = (d * slope) + offset
    n = np.sum(c)
    return n
def optional_cost_update_function(costs, parameters):
    ###defining a cost update function might look tricky but just need a bit
    ###of tenacity. And remember, this is optional, if you have a great guess for your costs you
    ###don't need to update the costs. Also, if you don't account for costs, this funciton is not needed
    from scipy.optimize import differential_evolution as devo
    print("Cost adjustment in progress...")
    print("old cost parameters: ",parameters)
    bounds = np.array([[0.001,10],[0.0001,10]])
    ###remove outliers:
    origins = []
    points = []
    motions = []
    c   = []
    cost_per_motion = []
    for i in range(len(costs)):
        origins.append(costs[i][0])
        points.append(costs[i][1])
        motions.append(abs(costs[i][0] - costs[i][1]))
        c.append(costs[i][2])
        cost_per_motion.append(costs[i][2]/optional_cost_function(costs[i][0],costs[i][1], parameters))
    mean_costs_per_distance = np.mean(np.asarray(cost_per_motion))
    sd = np.std(np.asarray(cost_per_motion))
    for element in cost_per_motion:
        if (
            element >= mean_costs_per_distance - 2.0 * sd
            and element <= mean_costs_per_distance + 2.0 * sd
        ):
            continue
        else:
            motions.pop(cost_per_motion.index(element))
            c.pop(cost_per_motion.index(element))
            origins.pop(cost_per_motion.index(element))
            points.pop(cost_per_motion.index(element))
            cost_per_motion.pop(cost_per_motion.index(element))
    def compute_l1_cost_misfit(params, origins,points, costs):
        parameters = {"offset": params[0], "slope": params[1]}
        sum1 = 0.0
        for idx in range(len(points)):
            sum1 = sum1 + (
                (optional_cost_function(origins[idx],points[idx],parameters) - costs[idx]) ** 2)
        return sum1
    res = devo(compute_l1_cost_misfit, bounds, args = (origins, points,c), tol=1e-6, disp=True, maxiter=300, popsize=20,polish=False)
    arguments = {"offset": res["x"][0],"slope": res["x"][1:]}
    print("New cost parameters: ", arguments)
    return arguments

In [4]:
import time
from gpcam.autonomous_experimenter import AutonomousExperimenterGP

def instrument(data):
    for entry in data:
        entry["value"] = np.sin(np.linalg.norm(entry["position"]))
        entry["cost"]  = [np.array([0,0]),entry["position"],np.sum(entry["position"])]
    return data
#initialization
#feel free to try different acquisition functions, e.g. optional_acq_func, "covariance", "shannon_ig"
#note how costs are defined in for the autonomous experimenter
my_ae = AutonomousExperimenterGP(np.array([[0,10],[0,10]]),instrument,
                                 np.ones((3)),np.array([[0.001,100],[0.001,100],[0.001,100]]),
                                 init_dataset_size= 20, acq_func = "shannon_ig", 
                                 #cost_func = optional_cost_function, 
                                 #cost_update_func = optional_cost_update_function,
                                 cost_func_params={"offset": 5.0,"slope":10.0})


print("length of the dataset: ",len(my_ae.x))

#training
#my_ae.train_async() #train asynchronously
my_ae.train()       #or not
#print("Initial training submitted")
#for i in range(2): #this loop shows how hyperparameters are changing if they are trained asynchronously
#    time.sleep(2)
my_ae.update_hps()


/home/marcus/VirtualEnvironments/gpCAM7/lib/python3.8/site-packages/numpy/core/_asarray.py:102: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  return array(a, dtype, copy=False, order=order)


New data communicated via tell()
CAUTION: you have not provided data variances in fvGP,
they will be set to 1 percent of the data values!
GP successfully initiated
Costs successfully initialized
##################################################################################
Initialization successfully concluded
now train(...) or train_async(...), and then go(...)
##################################################################################
length of the dataset:  20
fvGP training started with  20  data points
fvGP hyperparameter tuning in progress. Old hyperparameters:  [1. 1. 1.]  with old log likelihood:  21.549114090492374
method:  global
fvGP is performing a global differential evolution algorithm to find the optimal hyperparameters.
maximum number of iterations:  20
termination tolerance:  1e-06
bounds:  [[1.e-03 1.e+02]
 [1.e-03 1.e+02]
 [1.e-03 1.e+02]]
differential_evolution step 1: f(x)= 19.8209
differential_evolution step 2: f(x)= 19.8209
differential_evolution step 3

## Let's see what our initial model looks like

In [5]:
f = my_ae.gp_optimizer.posterior_mean(x_pred)["f(x)"]
f_re = f.reshape(100,100)

plot(x,y,f_re, data = np.column_stack([my_ae.x,my_ae.y]))

## Let's run the autonomus loop to 100 points

In [6]:
#run the loop
my_ae.go(N = 100, retrain_async_at = [30,50],)#,update_cost_func_at = [30])
print("length of the dataset is now: ", len(my_ae.x))
#and that runs the autonomous loop

Date and time:        2021-07-19_12_41_39



iteration:  20
Run Time:  0.00013375282287597656      seconds
Number of measurements:  20
hps:  [0.55958002 2.23456529 3.55664268]
ask() initiated with hyperparameters: [0.55958002 2.23456529 3.55664268]
optimization method:  global
bounds:  None
finding acquisition function maxima...
optimization method  global
tolerance:  1e-06
population size:  20
maximum number of iterations:  20
bounds: 
[[ 0 10]
 [ 0 10]]
cost function parameters:  {'offset': 5.0, 'slope': 10.0}
differential_evolution step 1: f(x)= -1.06706
differential_evolution step 2: f(x)= -1.07553
differential_evolution step 3: f(x)= -1.08154
differential_evolution step 4: f(x)= -1.08442
differential_evolution step 5: f(x)= -1.09593
differential_evolution step 6: f(x)= -1.09593
differential_evolution step 7: f(x)= -1.09593
differential_evolution step 8: f(x)= -1.09611
differential_evolution step 9: f(x)= -1.1001
differential_evolution step 10: f(x)= -1.1001
differential_evolution 

/home/marcus/VirtualEnvironments/gpCAM7/lib/python3.8/site-packages/numpy/core/_asarray.py:102: VisibleDeprecationWarning:

Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.



differential_evolution step 2: f(x)= -0.987566
differential_evolution step 3: f(x)= -0.993391
differential_evolution step 4: f(x)= -0.993391
acquisition funciton optimization tolerance changed to:  0.09933913285514465
Next points to be requested: 
[[5.74190758 0.11314239]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
New data communicated via tell()
fvGP data updated
GP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The autonomous experimenter is trying to update the huperparameters.
The autonomous experimenter could not find an instance of asynchronous training. Therefore, no update.
hps:  [0.53992139 2.16943714 3.60396455]



iteration:  23
Run Time:  0.46314239501953125      seconds
Number of measurements:  23
hps:  [0.53992139 2.16943714 3.60396455]
ask() initiated with hyperparameters: [0.53992

acquisition funciton optimization tolerance changed to:  0.04652811870651696
Next points to be requested: 
[[8.62431108 5.55662777]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
New data communicated via tell()
fvGP data updated
GP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The autonomous experimenter is trying to update the huperparameters.
The autonomous experimenter could not find an instance of asynchronous training. Therefore, no update.
hps:  [0.53992139 2.16943714 3.60396455]



iteration:  30
Run Time:  0.8392233848571777      seconds
Number of measurements:  30
hps:  [0.53992139 2.16943714 3.60396455]
ask() initiated with hyperparameters: [0.53992139 2.16943714 3.60396455]
optimization method:  global
bounds:  None
finding acquisition function maxima...
optimization method  global
toler

/home/marcus/VirtualEnvironments/gpCAM7/lib/python3.8/site-packages/numpy/core/_asarray.py:102: VisibleDeprecationWarning:

Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.



...

differential_evolution step 6: f(x)= -0.451084
differential_evolution step 7: f(x)= -0.49237
differential_evolution step 8: f(x)= -0.498615
differential_evolution step 9: f(x)= -0.498615
differential_evolution step 10: f(x)= -0.498615
differential_evolution step 11: f(x)= -0.498615
differential_evolution step 12: f(x)= -0.519156
differential_evolution step 13: f(x)= -0.519156
differential_evolution step 14: f(x)= -0.519156
differential_evolution step 15: f(x)= -0.519156
differential_evolution step 16: f(x)= -0.519156
differential_evolution step 17: f(x)= -0.519156
differential_evolution step 18: f(x)= -0.529236
differential_evolution step 19: f(x)= -0.529236
differential_evolution step 20: f(x)= -0.529236
acquisition funciton optimization tolerance changed to:  0.05292363227016921
Next points to be requested: 
[[1.06029647 0.00745823]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
New data communicated via tell()
fvGP da

differential_evolution step 6: f(x)= -0.356608
differential_evolution step 7: f(x)= -0.356608
differential_evolution step 8: f(x)= -0.356608
differential_evolution step 9: f(x)= -0.356608
differential_evolution step 10: f(x)= -0.356608
differential_evolution step 11: f(x)= -0.491378
differential_evolution step 12: f(x)= -0.491378
differential_evolution step 13: f(x)= -0.491378
differential_evolution step 14: f(x)= -0.491378
differential_evolution step 15: f(x)= -0.491378
differential_evolution step 16: f(x)= -0.493692
differential_evolution step 17: f(x)= -0.493692
differential_evolution step 18: f(x)= -0.495447
differential_evolution step 19: f(x)= -0.495447
differential_evolution step 20: f(x)= -0.495447
acquisition funciton optimization tolerance changed to:  0.04954469010147875
Next points to be requested: 
[[9.93774454 9.99797444]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
New data communicated via tell()
fvGP d

differential_evolution step 5: f(x)= -0.354646
differential_evolution step 6: f(x)= -0.35469
differential_evolution step 7: f(x)= -0.35469
differential_evolution step 8: f(x)= -0.35469
differential_evolution step 9: f(x)= -0.35469
differential_evolution step 10: f(x)= -0.35494
differential_evolution step 11: f(x)= -0.35494
differential_evolution step 12: f(x)= -0.356597
differential_evolution step 13: f(x)= -0.357282
differential_evolution step 14: f(x)= -0.357282
acquisition funciton optimization tolerance changed to:  0.03572817115708062
Next points to be requested: 
[[6.46233292 8.93457614]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
New data communicated via tell()
fvGP data updated
GP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The autonomous experimenter is trying to update the huperparam

differential_evolution step 6: f(x)= -0.306856
differential_evolution step 7: f(x)= -0.319754
differential_evolution step 8: f(x)= -0.319754
differential_evolution step 9: f(x)= -0.319754
differential_evolution step 10: f(x)= -0.324163
differential_evolution step 11: f(x)= -0.324999
differential_evolution step 12: f(x)= -0.33614
differential_evolution step 13: f(x)= -0.33614
differential_evolution step 14: f(x)= -0.338304
differential_evolution step 15: f(x)= -0.338304
differential_evolution step 16: f(x)= -0.339805
differential_evolution step 17: f(x)= -0.339805
differential_evolution step 18: f(x)= -0.339805
differential_evolution step 19: f(x)= -0.340192
acquisition funciton optimization tolerance changed to:  0.034019193043906173
Next points to be requested: 
[[6.22944986 6.23568764]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
New data communicated via tell()
fvGP data updated
GP data updated
+++++++++++++++++++++

differential_evolution step 7: f(x)= 44.4361
differential_evolution step 8: f(x)= 44.4361
differential_evolution step 9: f(x)= 44.4361
differential_evolution step 10: f(x)= 44.4361
differential_evolution step 11: f(x)= 44.2975
differential_evolution step 12: f(x)= 44.2975
differential_evolution step 13: f(x)= 43.9993
differential_evolution step 14: f(x)= 43.9993
differential_evolution step 15: f(x)= 43.6111
differential_evolution step 16: f(x)= 43.4814
differential_evolution step 17: f(x)= 43.4814
differential_evolution step 18: f(x)= 43.4814
differential_evolution step 19: f(x)= 43.4814
differential_evolution step 20: f(x)= 43.3092
fvGP found hyperparameters  [0.78358651 7.17595191 7.210738  ]  with likelihood  43.1870375332501  via global optimization
The autonomous experiment was concluded successfully
length of the dataset is now:  101


## Now let's plot the posterior mean after the experiment has concluded

In [7]:
res = my_ae.gp_optimizer.posterior_mean(x_pred)
f = res["f(x)"]
f = f.reshape(100,100)

plot(x,y,f, data = np.column_stack([my_ae.x,my_ae.y]))

## Running a Multi-Task GP Autonomous Data Acquisition
This example uses 21 (!) dim robot data and 7 tasks, which you can all use or pick a subset of them

In [8]:
##prepare some data
import numpy as np
from scipy.interpolate import griddata
data = np.load("sarcos.npy")
print(data.shape)
x = data[:,0:21]
y = data[:,21:23]

(4449, 28)


In [9]:
from gpcam.autonomous_experimenter import AutonomousExperimenterFvGP


def instrument(data):
    for entry in data:
        entry["values"] = griddata(x,y,entry["position"],method = "nearest", fill_value = 0)[0]
        entry["value positions"] = np.array([[0],[1]])
    return data

input_s = np.array([np.array([np.min(x[:,i]),np.max(x[:,i])]) for i in range(len(x[0]))])
print("index set (input space) bounds:")
print(input_s)
print("hps bounds:")
hps_bounds = np.empty((22,2))
hps_bounds[:,0] = 0.0001
hps_bounds[:,1] = 100.0
hps_bounds[0] = np.array([0.0001, 10000])
print(hps_bounds)
print("shape of y: ")
print(y.shape)

my_fvae = AutonomousExperimenterFvGP(input_s,2,1,instrument,np.ones((22)),hps_bounds,
                                     init_dataset_size= 10)
my_fvae.train()
my_fvae.go(N = 100)

index set (input space) bounds:
[[ -0.842481   0.661032]
 [ -0.939933  -0.085018]
 [ -0.46773    0.359348]
 [  0.797788   2.239407]
 [ -0.242241   1.278097]
 [ -0.919895   0.369078]
 [ -0.296364   0.686928]
 [ -4.771399   4.488624]
 [ -1.634053   2.289369]
 [ -2.884804   2.558282]
 [ -4.196409   3.734968]
 [ -3.067483   2.380553]
 [ -2.433971   1.978575]
 [ -3.180643   2.568279]
 [-48.072386  48.872604]
 [-25.585054  25.225171]
 [-24.697862  26.106756]
 [-36.19139   71.176937]
 [-38.485967  35.804308]
 [-22.103174  17.84188 ]
 [-36.502723  30.806254]]
hps bounds:
[[1.e-04 1.e+04]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]
 [1.e-04 1.e+02]]
shape of y: 
(4449, 2)
CAUTION: fvGP reports that you h

differential_evolution step 1: f(x)= -10.324
acquisition funciton optimization tolerance changed to:  1.0324016288541074
Next points to be requested: 
[[  0.61687711  -0.23625409   0.07421466   1.83316792  -0.1169978
   -0.15816332  -0.28439837   0.7691779    1.74979734   1.35691194
    0.61170676  -2.98596767  -2.27616337  -1.76371794 -46.39622886
   22.71465087  -4.55397582  61.48145288 -30.10750621  -1.12792124
   21.9190816 ]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
fvGP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The autonomous experimenter is trying to update the huperparameters.
The autonomous experimenter could not find an instance of asynchronous training. Therefore, no update.
hps:  [120.81401502  71.48587355  60.0046886   21.98734444  55.38420419
  78.0055675   76.14116125  87.632

differential_evolution step 1: f(x)= -9.92843
acquisition funciton optimization tolerance changed to:  0.992843446245371
Next points to be requested: 
[[ -0.37698749  -0.13893233   0.31000345   1.94020391   1.06712901
    0.2930342   -0.1919445   -3.09696113   1.18128169   1.07706203
   -3.47567635  -2.81331627  -0.48232132   0.61487667  47.76817593
  -23.4066452   14.78235384  42.54170995 -36.80411771  14.94923334
   19.62526364]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
fvGP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The autonomous experimenter is trying to update the huperparameters.
The autonomous experimenter could not find an instance of asynchronous training. Therefore, no update.
hps:  [120.81401502  71.48587355  60.0046886   21.98734444  55.38420419
  78.0055675   76.14116125  87.63

differential_evolution step 1: f(x)= -9.53076
acquisition funciton optimization tolerance changed to:  0.9530763909285369
Next points to be requested: 
[[ -0.22742154  -0.17086276   0.05219908   2.22276087   0.2120132
   -0.71374703   0.55307773   0.87097632   0.62980789  -2.05452063
   -1.41489361  -1.75197215  -0.24731926   1.70823954 -47.43362171
    5.87467905   3.37901616 -31.02028257 -32.9099972  -13.09964427
  -18.79497151]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
fvGP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
async training is being killed
no training to be killed
    Fresh optimization from scratch via global optimization
fvGP training started with  42  data points
fvGP hyperparameter tuning in progress. Old hyperparameters:  [120.81401502  71.48587355  60.0046886   21.98734444  55.38420419
  78.0055675   76.14116125  87.63249145  88.49189953  81.53170941

differential_evolution step 1: f(x)= -9.28014
acquisition funciton optimization tolerance changed to:  0.9280143507245948
Next points to be requested: 
[[ -0.64151912  -0.54444594   0.2346493    0.87380293   0.49295797
    0.21124911  -0.07851907   1.87551685  -0.08171408  -2.54905436
   -3.25851188  -2.30833026  -0.53898937   1.86855087 -25.35290154
   18.06958116  23.77481008  42.54544957 -33.49430076 -14.4757253
  -35.46479001]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
fvGP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The autonomous experimenter is trying to update the huperparameters.
The autonomous experimenter could not find an instance of asynchronous training. Therefore, no update.
hps:  [120.8462359   71.48589328  60.00469308  21.9874872   55.38422297
  78.00557751  76.1411679   87.63

...

acquisition funciton optimization tolerance changed to:  0.7141123109377836
Next points to be requested: 
[[ 4.41748629e-01 -5.80270137e-01 -1.92077546e-01  1.83287213e+00
   9.39110187e-01  4.67503229e-02  2.46229362e-01  2.07814782e+00
   1.71121754e+00  1.27413143e+00  3.25133217e+00  8.66143084e-01
  -1.67235270e+00 -2.31793022e+00  4.86703235e+01 -2.51996093e+01
   1.24579459e+01  5.39562825e+01  3.12581759e+00  5.89127885e+00
  -2.45774322e+01]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
fvGP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The autonomous experimenter is trying to update the huperparameters.
The autonomous experimenter could not find an instance of asynchronous training. Therefore, no update.
hps:  [121.34525417  71.48608585  60.00469138  21.98773256  55.38429348
  78.00548617

differential_evolution step 1: f(x)= -8.41322
acquisition funciton optimization tolerance changed to:  0.8413221951946968
Next points to be requested: 
[[ -0.19081497  -0.73034124  -0.37330899   1.14705405  -0.05429161
   -0.42514814   0.11646672   3.86455807   0.18034192  -0.31170225
   -3.08998602  -0.24053543   0.45201113   0.48244298   8.03279774
   17.94440476   9.43079479 -35.87367151  31.89014058 -14.54605228
   21.90249279]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
fvGP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The autonomous experimenter is trying to update the huperparameters.
The autonomous experimenter could not find an instance of asynchronous training. Therefore, no update.
hps:  [121.34525417  71.48608585  60.00469138  21.98773256  55.38429348
  78.00548617  76.14113321  87.6

differential_evolution step 1: f(x)= -8.2823
acquisition funciton optimization tolerance changed to:  0.8282303765516676
Next points to be requested: 
[[ 4.77072233e-01 -8.73966133e-01 -1.26706566e-01  1.85006144e+00
  -6.81427090e-03 -8.44057449e-01  5.72861797e-01 -3.22100311e+00
   2.01901117e+00 -2.75486674e-02  1.53917471e-01 -1.93658078e+00
  -2.15920066e+00  1.83961433e+00  4.33910828e+01  1.82238208e+01
  -1.72614160e+01 -1.63721243e+01  3.47199925e+01  1.66962745e+01
   2.67021238e+01]]
Sending request to instrument ...
Data received
Checking if data is clean ...
done
Communicating new data to GP
fvGP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The autonomous experimenter is trying to update the huperparameters.
The autonomous experimenter could not find an instance of asynchronous training. Therefore, no update.
hps:  [121.34525417  71.48608585  60.004

Data received
Checking if data is clean ...
done
Communicating new data to GP
fvGP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The autonomous experimenter is trying to update the huperparameters.
The autonomous experimenter could not find an instance of asynchronous training. Therefore, no update.
hps:  [121.34525417  71.48608585  60.00469138  21.98773256  55.38429348
  78.00548617  76.14113321  87.63238923  88.49088066  81.53214531
  81.36457609  48.91217763  35.18121156  90.41603432  78.87175049
  26.13952739  99.10512936  84.24672031  62.15984413  97.0881395
  88.08322787  99.37973933]



iteration:  96
Run Time:  33.92343282699585      seconds
Number of measurements:  96
hps:  [121.34525417  71.48608585  60.00469138  21.98773256  55.38429348
  78.00548617  76.14113321  87.63238923  88.49088066  81.53214531
  81.36457609  48.91217763  35.18121156  90.41603432

Data received
Checking if data is clean ...
done
Communicating new data to GP
fvGP data updated
++++++++++++++++++++++++++
|Training ...            |
++++++++++++++++++++++++++
    No training in this round but I am trying to update the hyperparameters
The autonomous experimenter is trying to update the huperparameters.
The autonomous experimenter could not find an instance of asynchronous training. Therefore, no update.
hps:  [121.34525417  71.48608585  60.00469138  21.98773256  55.38429348
  78.00548617  76.14113321  87.63238923  88.49088066  81.53214531
  81.36457609  48.91217763  35.18121156  90.41603432  78.87175049
  26.13952739  99.10512936  84.24672031  62.15984413  97.0881395
  88.08322787  99.37973933]



iteration:  99
Run Time:  35.869059562683105      seconds
Number of measurements:  99
hps:  [121.34525417  71.48608585  60.00469138  21.98773256  55.38429348
  78.00548617  76.14113321  87.63238923  88.49088066  81.53214531
  81.36457609  48.91217763  35.18121156  90.4160343

## Plotting the 0th task in a 2d slice

In [10]:
x_pred = np.zeros((10000,21))
x = np.linspace(input_s[0,0],input_s[0,1],100)
y = np.linspace(input_s[1,0],input_s[1,1],100)
x,y = np.meshgrid(x,y)
counter = 0
for i in  range(100):
    for j in range(100):
        x_pred[counter] = np.zeros((21))
        x_pred[counter,[0,1]] = np.array([x[i,j],y[i,j]])
        counter += 1
res = my_fvae.gp_optimizer.posterior_mean(x_pred)
f = res["f(x)"]
f = f.reshape(100,100)

plot(x,y,f)

## Back to a single task: using the GPOptimizer class directly gives you some more flexibility
We will show more soon!

In [11]:
#/usr/bin/env python
import numpy as np
from gpcam.gp_optimizer import GPOptimizer

#initialize some data
x_data = np.random.uniform(size = (100,1))
y_data = np.sin(x_data)[:,0]


#initialize the GPOptimizer
my_gpo = GPOptimizer(1,np.array([[0,1]]))
#tell() it some data
my_gpo.tell(x_data,y_data)
#initialize a GP ...
my_gpo.init_gp(np.ones(2))
#and train it
my_gpo.train_gp(np.array([[0.001,100],[0.001,100]]))

#let's make a prediction
print(my_gpo.posterior_mean(np.array([0.44])))

#now we can ask for a new point
r = my_gpo.ask()
print(r)
#putting the ask() in a loop and updating the data will
#give you all you need for your autonomous experiment

New data communicated via tell()
CAUTION: you have not provided data variances in fvGP,
they will be set to 1 percent of the data values!
GP successfully initiated
fvGP training started with  100  data points
fvGP hyperparameter tuning in progress. Old hyperparameters:  [1. 1.]  with old log likelihood:  -96.20977324654486
method:  global
fvGP is performing a global differential evolution algorithm to find the optimal hyperparameters.
maximum number of iterations:  120
termination tolerance:  1e-06
bounds:  [[1.e-03 1.e+02]
 [1.e-03 1.e+02]]
differential_evolution step 1: f(x)= -155.961
differential_evolution step 2: f(x)= -156.04
differential_evolution step 3: f(x)= -156.04
differential_evolution step 4: f(x)= -156.298
differential_evolution step 5: f(x)= -156.298
differential_evolution step 6: f(x)= -156.414
differential_evolution step 7: f(x)= -156.414
differential_evolution step 8: f(x)= -156.678
differential_evolution step 9: f(x)= -156.8
differential_evolution step 10: f(x)= -156